In [1]:
from re import M
import re
import pandas as pd

movies_df = pd.read_csv('movies.csv')

In [2]:
print(movies_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10866 entries, 0 to 10865
Data columns (total 21 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   id                    10866 non-null  int64  
 1   imdb_id               10856 non-null  object 
 2   popularity            10866 non-null  float64
 3   budget                10866 non-null  int64  
 4   revenue               10866 non-null  int64  
 5   original_title        10866 non-null  object 
 6   cast                  10790 non-null  object 
 7   homepage              2936 non-null   object 
 8   director              10822 non-null  object 
 9   tagline               8042 non-null   object 
 10  keywords              9373 non-null   object 
 11  overview              10862 non-null  object 
 12  runtime               10866 non-null  int64  
 13  genres                10843 non-null  object 
 14  production_companies  9836 non-null   object 
 15  release_date       

#### Handling null values

In [3]:
print(movies_df.isnull().sum()) 

id                         0
imdb_id                   10
popularity                 0
budget                     0
revenue                    0
original_title             0
cast                      76
homepage                7930
director                  44
tagline                 2824
keywords                1493
overview                   4
runtime                    0
genres                    23
production_companies    1030
release_date               0
vote_count                 0
vote_average               0
release_year               0
budget_adj                 0
revenue_adj                0
dtype: int64


In [4]:
for column in ['imdb_id','cast', 'director', 'keywords', 'overview', 'genres', 'production_companies','homepage','tagline']:
    movies_df[column].fillna('N/A', inplace=True)
movies_df.head(5)

id    imdb_id  popularity     budget     revenue  \
0  135397  tt0369610   32.985763  150000000  1513528810   
1   76341  tt1392190   28.419936  150000000   378436354   
2  262500  tt2908446   13.112507  110000000   295238201   
3  140607  tt2488496   11.173104  200000000  2068178225   
4  168259  tt2820852    9.335014  190000000  1506249360   

                 original_title  \
0                Jurassic World   
1            Mad Max: Fury Road   
2                     Insurgent   
3  Star Wars: The Force Awakens   
4                     Furious 7   

                                                cast  \
0  Chris Pratt|Bryce Dallas Howard|Irrfan Khan|Vi...   
1  Tom Hardy|Charlize Theron|Hugh Keays-Byrne|Nic...   
2  Shailene Woodley|Theo James|Kate Winslet|Ansel...   
3  Harrison Ford|Mark Hamill|Carrie Fisher|Adam D...   
4  Vin Diesel|Paul Walker|Jason Statham|Michelle ...   

                                            homepage          director  \
0                      http://www.jurassicworld.com/   Colin Trevorrow   
1                        http://www.madmaxmovie.com/     George Miller   
2     http://www.thedivergentseries.movie/#insurgent  Robert Schwentke   
3  http://www.starwars.com/films/star-wars-episod...       J.J. Abrams   
4                           http://www.furious7.com/         James Wan   

                         tagline  ...  \
0              The park is open.  ...   
1             What a Lovely Day.  ...   
2     One Choice Can Destroy You  ...   
3  Every generation has a story.  ...   
4            Vengeance Hits Home  ...   

                                            overview runtime  \
0  Twenty-two years after the events of Jurassic ...     124   
1  An apocalyptic story set in the furthest reach...     120   
2  Beatrice Prior must confront her inner demons ...     119   
3  Thirty years after defeating the Galactic Empi...     136   
4  Deckard Shaw seeks revenge against Dominic Tor...     137   

                                      genres  \
0  Action|Adventure|Science Fiction|Thriller   
1  Action|Adventure|Science Fiction|Thriller   
2         Adventure|Science Fiction|Thriller   
3   Action|Adventure|Science Fiction|Fantasy   
4                      Action|Crime|Thriller   

                                production_companies release_date vote_count  \
0  Universal Studios|Amblin Entertainment|Legenda...       6/9/15       5562   
1  Village Roadshow Pictures|Kennedy Miller Produ...      5/13/15       6185   
2  Summit Entertainment|Mandeville Films|Red Wago...      3/18/15       2480   
3          Lucasfilm|Truenorth Productions|Bad Robot     12/15/15       5292   
4  Universal Pictures|Original Film|Media Rights ...       4/1/15       2947   

   vote_average  release_year    budget_adj   revenue_adj  
0           6.5          2015  1.379999e+08  1.392446e+09  
1           7.1          2015  1.379999e+08  3.481613e+08  
2           6.3          2015  1.012000e+08  2.716190e+08  
3           7.5          2015  1.839999e+08  1.902723e+09  
4           7.3          2015  1.747999e+08  1.385749e+09  

[5 rows x 21 columns]

In [5]:
print(movies_df.isnull().sum())  

id                      0
imdb_id                 0
popularity              0
budget                  0
revenue                 0
original_title          0
cast                    0
homepage                0
director                0
tagline                 0
keywords                0
overview                0
runtime                 0
genres                  0
production_companies    0
release_date            0
vote_count              0
vote_average            0
release_year            0
budget_adj              0
revenue_adj             0
dtype: int64


#### Handling multiple date formats

In [6]:
# The different date formats in the 'release_date' column
def identify_date_format(date):
    formats = {
        r'^\d{4}-\d{2}-\d{2}$': 'YYYY-MM-DD',
        r'^\d{2}/\d{2}/\d{4}$': 'MM/DD/YYYY',
        r'^\d{2}/\d{2}/\d{2}$': 'MM/DD/YY',
        r'^\d{1,2}\s\w+\s\d{4}$': 'DD Month YYYY',
        r'^\d{1,2}.\d{1,2}.\d{4}$': 'DD.MM.YYYY',
        r'^\d{4}.\d{1,2}.\d{1,2}$': 'YYYY.MM.DD',
        r'^\d{1,2}.\d{1,2}.\d{2}$': 'DD.MM.YY',
        r'^\w+\s\d{1,2},\s\d{4}$': 'Month DD, YYYY',
        r'^\w+\s\d{1,2}th,\s\d{4}$': 'Month DDth, YYYY',
    }

    for pattern, format_name in formats.items():
        if re.match(pattern, date):
            return format_name
    return 'Unknown format'

df = pd.DataFrame(movies_df['release_date'])

df['date_format'] = df['release_date'].apply(identify_date_format)

unique_formats = df['date_format'].unique()
print(df)
print("Unique date formats:", unique_formats)

      release_date date_format
0           6/9/15    DD.MM.YY
1          5/13/15    DD.MM.YY
2          3/18/15    DD.MM.YY
3         12/15/15    MM/DD/YY
4           4/1/15    DD.MM.YY
...            ...         ...
10861      6/15/66    DD.MM.YY
10862     12/21/66    MM/DD/YY
10863       1/1/66    DD.MM.YY
10864      11/2/66    DD.MM.YY
10865     11/15/66    MM/DD/YY

[10866 rows x 2 columns]
Unique date formats: ['DD.MM.YY' 'MM/DD/YY']


In [7]:
movies_df['release_date'] = pd.to_datetime(movies_df['release_date'], errors='coerce')

In [8]:
movies_df['release_date'] = pd.to_datetime(movies_df['release_date'], errors='coerce')

movies_df['release_date'] = movies_df['release_date'].dt.strftime('%Y-%m-%d') 
df = pd.DataFrame(movies_df['release_date'])
df['date_format'] = df['release_date'].apply(identify_date_format)

unique_formats = df['date_format'].unique()
print(df)
print("Unique date formats:", unique_formats)

      release_date date_format
0       2015-06-09  YYYY-MM-DD
1       2015-05-13  YYYY-MM-DD
2       2015-03-18  YYYY-MM-DD
3       2015-12-15  YYYY-MM-DD
4       2015-04-01  YYYY-MM-DD
...            ...         ...
10861   2066-06-15  YYYY-MM-DD
10862   2066-12-21  YYYY-MM-DD
10863   2066-01-01  YYYY-MM-DD
10864   2066-11-02  YYYY-MM-DD
10865   2066-11-15  YYYY-MM-DD

[10866 rows x 2 columns]
Unique date formats: ['YYYY-MM-DD']


#### replacing separant '|' with ','

In [9]:
#separated the genres,production_companies and cast using ','
movies_df['genres'] = movies_df['genres'].apply(lambda g: g.replace('|', ', '))
movies_df['production_companies']= movies_df['production_companies'].apply(lambda x: x.replace('|', ', '))
movies_df['cast']= movies_df['cast'].apply(lambda c: c.replace('|', ', '))
movies_df['director']= movies_df['director'].apply(lambda c: c.replace('|', ', '))
movies_df['keywords']= movies_df['keywords'].apply(lambda c: c.replace('|', ', '))
comma_sep = movies_df.loc[:, ['genres', 'production_companies', 'cast','director']]
comma_sep.head()

genres  \
0  Action, Adventure, Science Fiction, Thriller   
1  Action, Adventure, Science Fiction, Thriller   
2          Adventure, Science Fiction, Thriller   
3   Action, Adventure, Science Fiction, Fantasy   
4                       Action, Crime, Thriller   

                                production_companies  \
0  Universal Studios, Amblin Entertainment, Legen...   
1  Village Roadshow Pictures, Kennedy Miller Prod...   
2  Summit Entertainment, Mandeville Films, Red Wa...   
3        Lucasfilm, Truenorth Productions, Bad Robot   
4  Universal Pictures, Original Film, Media Right...   

                                                cast          director  
0  Chris Pratt, Bryce Dallas Howard, Irrfan Khan,...   Colin Trevorrow  
1  Tom Hardy, Charlize Theron, Hugh Keays-Byrne, ...     George Miller  
2  Shailene Woodley, Theo James, Kate Winslet, An...  Robert Schwentke  
3  Harrison Ford, Mark Hamill, Carrie Fisher, Ada...       J.J. Abrams  
4  Vin Diesel, Paul Walker, Jason Statham, Michel...         James Wan

#### Normalizing popularity

In [10]:
#popularity column before preprocessing
movies_df['popularity'].head()

0    32.985763
1    28.419936
2    13.112507
3    11.173104
4     9.335014
Name: popularity, dtype: float64

In [11]:
# Normalize popularity
#popularity after preprocessing
movies_df['popularity']=1+9*(movies_df['popularity'] - movies_df['popularity'].min())/(movies_df['popularity'].max()-movies_df['popularity'].min())
movies_df['popularity'].head()

0    10.000000
1     8.754235
2     4.577671
3     4.048514
4     3.546999
Name: popularity, dtype: float64

In [12]:
#cleaned and preprocessed dataset
print(movies_df.head(10))

       id    imdb_id  popularity     budget     revenue  \
0  135397  tt0369610   10.000000  150000000  1513528810   
1   76341  tt1392190    8.754235  150000000   378436354   
2  262500  tt2908446    4.577671  110000000   295238201   
3  140607  tt2488496    4.048514  200000000  2068178225   
4  168259  tt2820852    3.546999  190000000  1506249360   
5  281957  tt1663202    3.485796  135000000   532950503   
6   87101  tt1340138    3.361285  155000000   440603537   
7  286217  tt3659388    3.091998  108000000   595380321   
8  211672  tt2293640    3.020176   74000000  1156730962   
9  150540  tt2096673    2.726222  175000000   853708609   

                 original_title  \
0                Jurassic World   
1            Mad Max: Fury Road   
2                     Insurgent   
3  Star Wars: The Force Awakens   
4                     Furious 7   
5                  The Revenant   
6            Terminator Genisys   
7                   The Martian   
8                       Minions   


#### Replacing special characters

In [13]:
dir_lst = movies_df['director'].tolist()
print(len(dir_lst))

10866


In [14]:
import re

def clean_encoded_name(encoded_name):
    # Replace known problematic character sequences for both names
    cleaned_name = encoded_name.replace("Ã¼", "ü")  \
                                .replace("Ã…Â¡", "š") \
                                .replace("Ã€", "Ãe")  \
                                .replace("ÃƒÂ©", "é") \
                                .replace("ÃƒÂº", "ú") \
                                .replace("ÃƒÂ¡", "á") \
                                .replace("ÃƒÂ±", "ñ") \
                                .replace("ÃƒÂ", "Ó") \
                                .replace("ÃƒÂ¡", "á") \
                                .replace("ÃƒÂº", "ú") \
                                .replace("ÃƒÂ¡", "á") \
                                .replace("ÃƒÂ½", "ý") \
                                .replace("ÃƒÂ¤", "ä") \
                                .replace("Ã¡", "á") \
                                .replace("Ã­", "í") \
                                .replace("Ã¡", "á") \
                                .replace("Ã©", "é") \
                                .replace("Ã“", "Ó") \
                                .replace("Ã‰", "É") \
                                .replace("Ã–", "Ö") \
                                .replace("Ã‡", "Ç") \
                                .replace("ÄŸ", "ğ") \
                                .replace("Å™", "ř") \
                                .replace("Ã­", "í")  \
                                .replace("Ã³", "ó")

    # Further cleanup using regex for additional patterns
    cleaned_name = re.sub(r"Ã(.)", lambda x: chr(ord(x.group(1)) + 0x60), cleaned_name)

    return cleaned_name

# Original strings with encoding issues
encoded_names = [
    "Alejandro GonzÃƒÂ¡lez IÃƒÂ±ÃƒÂ¡rritu",
    "KryÃ…Â¡tof HÃƒÂ¡dek",
    "Aki KaurismÃƒÂ¤ki",
    "JosÃƒÂ© ZÃƒÂºÃƒÂ±iga",
    "Cheung Yam-Yim",
    "Ã€lex BrendemÃ¼hl",
    "TÃ³mas Lemarquis",
    "Irene MontalÃ",
    "FÃ©lix GÃ³mez",
    "Ã‰tienne Chatiliez",
    "Ã‡aÄŸan Irmak",
    "JiÅ™Ã­ Menzel"
]

# Clean both names
for name in encoded_names:
    print(clean_encoded_name(name))


Alejandro González Iñárritu
Kryštof Hádek
Aki KaurismÓ¤ki
José Zúñiga
Cheung Yam-Yim
Ålex Brendemühl
Tómas Lemarquis
Irene MontalÃ
Félix Gómez
Étienne Chatiliez
Çağan Irmak
Jiří Menzel


In [15]:
special_chars = []
all_directors = []
for named in dir_lst:
  flag = 0

  name = clean_encoded_name(named)
  all_names = [name.strip() for name in name.split(",")]
  for i in range(len(name)):
    val = ord(name[i])
    if (val >= 65 and val <= 90) or (val >= 97 and val <= 122) or name[i] in [" ", ",", "."]:
      continue
    else:
      flag = 1
      if i + 1 < len(name) :
        new_val = ord(name[i+1])
        new_str = ""
        if not ( (new_val >= 65 and new_val <= 90) or (new_val >= 97 and new_val <= 122) or name[i+1] in [" ", ",", "."] ):
          new_str = name[i] + name[i+1]
          special_chars.append(new_str)
        else:
          special_chars.append(name[i])
      else:
        special_chars.append(name[i])
      # break
  if flag == 1:
    pass
    # print(name)
  all_directors.extend(all_names)

new_spec_chars = list(set(special_chars))
print(len(special_chars), special_chars)
print(len(new_spec_chars), new_spec_chars)
print(len(all_directors), all_directors)

all_unique_directors = list(set(all_directors))
print(len(all_unique_directors), all_unique_directors)

  # if "," in name:
  #   names = name.split(',')
  # else:
  #   names = [name]
  # Ã¡ Ã\ Ã¨ Ã³ Ã© Ã¶ Ã¥

707 ['á', 'đá', 'á', '-', '-', 'á', '-', 'é', '-', '-', 'ó', 'á', 'é', 'Î', 'é', '-', '-', '-', 'ć', '-', 'é', 'é', 'Ą', 'Ę', '-', '₆', 'á', 'á', 'é', 'é', '/', "'", 'Ċ', '/', 'é', 'é', '/', 'á', 'đá', 'á', '-', '-', 'áđ', 'đ', 'ċ', 'é', '-', 'é', 'Ė', 'Ĕ', 'ć', 'é', '-', 'Ą', 'í', 'í', 'Ĕ', 'é', 'í', '\t', '-', '-', 'í', 'í', '-', 'é', '-', '/', '-', "'", '/', "'", 'á', '-', 'á', 'í', '-', '-', 'é', "'", '-', 'é', '/', 'Äá', 'á', 'á', '-', 'í', '/', '-', 'é', 'é', 'é', '-', 'Ę', "'", 'é', '9', '/', '-', "'", "'", 'Ė', '-', '-', "'", '-', 'é', 'é', 'í', '-', 'á', '₆', 'ó', 'Å', 'é', 'Ė', '-', 'í', '-', 'ó', '-', '-', 'Ì', 'đá', 'á', '-', "'", "'", 'é', 'Ä‡', '‡', 'ć', 'Ĉ', "'", '-', '-', "'", 'é', '/', '\t', '/', '/', 'ć', 'é', 'é', 'é', 'é', "'", 'é', 'ó', 'Ė', 'é', 'Ė', 'ą', 'ą', 'é', 'í', 'í', 'Ĕ', 'ą', 'Ė', '-', 'Ą', '-', '/', 'á', 'Ä‡', '‡', '/', '/', '-', 'ğ', 'Ì', "'", 'Ä±', '±', 'Ä±', '±', 'Ä±', '±', 'ü', '/', '-', '/', '-', 'Å', '-', '-', '-', 'Ĉ', '-', 'É', '/', '-', '/', '/'

In [16]:
# pip install unidecode
# #
all_unique_directors.sort()
all_unique_directors_dict =  {}
director_df = pd.DataFrame( { "ID" : range(1, len(all_unique_directors) + 1),
                              "Name" : all_unique_directors} )

all_unique_directors_dict = dict(zip(director_df['Name'], director_df['ID']))
print(all_unique_directors_dict)
print(director_df.head())
print(director_df.tail(20))




{'A. Todd Smith': 1, 'A.R. Murugadoss': 2, 'Aaron Aites': 3, 'Aaron Blaise': 4, 'Aaron Hann': 5, 'Aaron Harvey': 6, 'Aaron Katz': 7, 'Aaron Keeling': 8, 'Aaron Moorhead': 9, 'Aaron Norris': 10, 'Aaron Schneider': 11, 'Aaron Seelman': 12, 'Aaron Seltzer': 13, 'Aaron Woodley': 14, 'Abbas Alibhai Burmawalla': 15, 'Abbas Kiarostami': 16, 'Abbas Tyrewala': 17, 'Abe Levy': 18, 'Abe Sylvia': 19, 'Abel Ferrara': 20, 'Abel Ferry': 21, 'Adam Brooks': 22, 'Adam Curtis': 23, 'Adam Deacon': 24, 'Adam Doench': 25, 'Adam Egypt Mortimer': 26, 'Adam Elliot': 27, 'Adam Fields': 28, 'Adam Gierasch': 29, 'Adam Green': 30, 'Adam Grossman': 31, 'Adam Jay Epstein': 32, 'Adam Kassen': 33, 'Adam MacDonald': 34, 'Adam Marcus': 35, 'Adam Mason': 36, 'Adam Massey': 37, 'Adam McKay': 38, 'Adam Neutzsky-Wulff': 39, 'Adam Rehmeier': 40, 'Adam Rifkin': 41, 'Adam Robitel': 42, 'Adam Rogers': 43, 'Adam Salky': 44, 'Adam Schindler': 45, 'Adam Shankman': 46, 'Adam Wingard': 47, 'Adamo P. Cultraro': 48, 'Adolfo Alix Jr.':

In [17]:
movie_director_df = pd.DataFrame(columns=["movie_id", "director_id"])
# movie_director_df.head()

for index , row in movies_df.iterrows():
  movie_id = row['id']
  directors = row['director']
  # print(movie_id, directors)
  name = clean_encoded_name(directors)
  all_name_in_row = [name.strip() for name in name.split(",")]
  # print(all_name_in_row)
  for names in all_name_in_row:
    # Create a new row as a DataFrame
    # print(movie_id, names, all_unique_directors_dict[names])
    new_row = pd.DataFrame({'movie_id':movie_id , 'director_id': [all_unique_directors_dict[names]]})
    movie_director_df = pd.concat([movie_director_df, new_row], ignore_index=True)
    # print(movie_director_df.head())
    # movie_director_df = movie_director_df.append({'movie_id': movie_id, 'director_id': all_unique_directors_dict[names]}, ignore_index=True)

print(movie_director_df.shape)
movie_director_df.head(15)




(11954, 2)


movie_id director_id
0    135397         962
1     76341        1780
2    262500        4362
3    140607        2068
4    168259        2186
5    281957         123
6     87101         102
7    286217        4264
8    211672        3008
9    211672        4093
10   150540        3971
11   206647        4516
12    76757        3022
13    76757        3127
14   264660         137

In [18]:
actor_lst = movies_df['cast'].tolist()
print(len(actor_lst))

10866


In [19]:
special_chars = []
all_actors = []
for named in actor_lst:
  flag = 0
  # name = named
  name = clean_encoded_name(named)
  all_names = [name.strip() for name in name.split(",")]
  for i in range(len(name)):
    val = ord(name[i])
    if (val >= 65 and val <= 90) or (val >= 97 and val <= 122) or name[i] in [" ", ",", "."]:
      continue
    else:
      flag = 1
      if i + 1 < len(name) :
        new_val = ord(name[i+1])
        new_str = ""
        if not ( (new_val >= 65 and new_val <= 90) or (new_val >= 97 and new_val <= 122) or name[i+1] in [" ", ",", "."] ):
          new_str = name[i] + name[i+1]
          special_chars.append(new_str)
        else:
          special_chars.append(name[i])
      else:
        special_chars.append(name[i])
      # break
  if flag == 1:
    pass
    # print(name)
  all_actors.extend(all_names)

new_spec_chars = list(set(special_chars))
print(len(special_chars), special_chars)
print(len(new_spec_chars), new_spec_chars)
print(len(all_actors), all_actors)

all_unique_actors = list(set(all_actors))
print(len(all_unique_actors), all_unique_actors)

  # if "," in name:
  #   names = name.split(',')
  # else:
  #   names = [name]
  # Ã¡ Ã\ Ã¨ Ã³ Ã© Ã¶ Ã¥

3040 ["'", '-', 'đ', 'é', 'á', '50', '0', "'", '-', '-', "'", "'", 'Ó', 'Ó', 'í', '-', 'é', 'í', 'í', '-', 'Ä', '-', '-', '-', 'á', 'ċ', 'ċ', '-', "'", 'Ä‡', '‡', 'í', '-', 'é', 'í', "'", 'é', '-', 'ą', 'é', '-', '-', '-', '-', 'Ä‡', '‡', 'é', '-', 'é', 'đ', '-', 'é', 'é', 'é', "'", 'é', '-', "'", '-', 'ü', 'ą', '-', '-', '-', 'é', 'ċ', '-', "'", '₆', 'é', "'", "'", '-', 'ó', 'é', "'", "'", '"', '"', '-', 'é', 'é', '-', "'", '/', "'", 'é', 'é', "'", "'", 'é', 'Å', '-', 'á', '-', 'é', '-', '/', 'á', '/', 'Ĉ', '-', '-', 'é', 'é', '-', '-', "'", '/', '/', "'", 'ć', 'é', "'", '/', 'é', 'é', '/', "'", 'é', 'é', '-', '/', "'", 'đ', '-', '-', 'ċ', '-', "'", 'ą', 'ċ', "'", '-', 'ċ', 'Ĉ', '-', 'Ę', '-', '-', '-', '-', 'é', 'í', '-', "'", 'é', 'é', '-', '-', 'é', '-', '-', 'é', "'", 'ó', 'í', '-', 'ó', "'", 'ć', 'é', 'é', '-', 'ċ', 'đ', 'Å¡', '¡', 'á', '-', 'ą', 'é', "'", '-', "'", 'Ä‡', '‡', '-', "'", 'Ĉ', '-', 'ü', "'", 'í', 'ċ', "'", "'", '-', '-', "'", "'", 'é', 'í', 'í', 'á', '-', 'á', '-',

In [20]:
all_unique_actors.sort()
all_unique_actors_dict =  {}
actor_df = pd.DataFrame( { "ID" : range(1, len(all_unique_actors) + 1),
                              "Name" : all_unique_actors} )

all_unique_actors_dict = dict(zip(actor_df['Name'], actor_df['ID']))
print(all_unique_actors_dict)
print(actor_df.head())
print(actor_df.tail())

{'"Weird Al" Yankovic': 1, '50 Cent': 2, 'A Martinez': 3, 'A. J. Langer': 4, 'A. Michael Baldwin': 5, 'A.J. Buckley': 6, 'A.J. Cook': 7, 'AJ Bowen': 8, 'AJ Michalka': 9, 'Aaliyah': 10, 'Aamir Khan': 11, 'Aanjjan Srivastav': 12, 'Aaran Thomas': 13, 'Aarif Lee': 14, 'Aaron Abrams': 15, 'Aaron Ashmore': 16, 'Aaron Barr': 17, 'Aaron Burns': 18, 'Aaron Dessner': 19, 'Aaron Douglas': 20, 'Aaron Eckhart': 21, 'Aaron Hughes': 22, 'Aaron Jeffery': 23, 'Aaron Kwok': 24, 'Aaron Michael Davies': 25, 'Aaron Milo': 26, 'Aaron Murphy': 27, "Aaron O'Connell": 28, 'Aaron Paul': 29, 'Aaron Pedersen': 30, 'Aaron Poole': 31, 'Aaron Ringhiser-Carlson': 32, 'Aaron Ruell': 33, 'Aaron Schwartz': 34, 'Aaron Spann': 35, 'Aaron Stanford': 36, 'Aaron Staton': 37, 'Aaron Swartz': 38, 'Aaron Taylor-Johnson': 39, 'Aaron Tveit': 40, 'Aaron Wolff': 41, 'Aaron Yoo': 42, 'Aarti Mann': 43, 'Aasha Davis': 44, 'Aasif Mandvi': 45, 'Abbes Zahmani': 46, 'Abbey DiGregorio': 47, 'Abbie Cornish': 48, 'Abbie Salt': 49, 'Abby Elli

In [21]:
movie_actor_df = pd.DataFrame(columns=["movie_id", "actor_id"])
for index , row in movies_df.iterrows():
  movie_id = row['id']
  actors = row['cast']
  name = clean_encoded_name(actors)
  all_name_in_row = [name.strip() for name in name.split(",")]
  for names in all_name_in_row:
    new_row = pd.DataFrame({'movie_id':movie_id , 'actor_id': [all_unique_actors_dict[names]]})
    movie_actor_df = pd.concat([movie_actor_df, new_row], ignore_index=True)

print(movie_actor_df.shape)
movie_actor_df.head(15)

(52698, 2)


movie_id actor_id
0    135397     3244
1    135397     2537
2    135397     7369
3    135397    18422
4    135397    13583
5     76341    17882
6     76341     3056
7     76341     7180
8     76341    13527
9     76341     9428
10   262500    16464
11   262500    17623
12   262500     9929
13   262500     1227
14   262500    13034

In [22]:
genre_lst = movies_df['genres'].tolist()
print(len(genre_lst))

10866


In [23]:
special_chars = []
all_genres = []
for named in genre_lst:
  flag = 0
  # name = named
  name = clean_encoded_name(named)
  all_names = [name.strip() for name in name.split(",")]
  for i in range(len(name)):
    val = ord(name[i])
    if (val >= 65 and val <= 90) or (val >= 97 and val <= 122) or name[i] in [" ", ",", "."]:
      continue
    else:
      flag = 1
      if i + 1 < len(name) :
        new_val = ord(name[i+1])
        new_str = ""
        if not ( (new_val >= 65 and new_val <= 90) or (new_val >= 97 and new_val <= 122) or name[i+1] in [" ", ",", "."] ):
          new_str = name[i] + name[i+1]
          special_chars.append(new_str)
        else:
          special_chars.append(name[i])
      else:
        special_chars.append(name[i])
      # break
  if flag == 1:
    pass
    # print(name)
  all_genres.extend(all_names)

new_spec_chars = list(set(special_chars))
print(len(special_chars), special_chars)
print(len(new_spec_chars), new_spec_chars)
print(len(all_genres), all_genres)

all_unique_genres = list(set(all_genres))
print(len(all_unique_genres), all_unique_genres)

  # if "," in name:
  #   names = name.split(',')
  # else:
  #   names = [name]
  # Ã¡ Ã\ Ã¨ Ã³ Ã© Ã¶ Ã¥

23 ['/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/']
1 ['/']
26983 ['Action', 'Adventure', 'Science Fiction', 'Thriller', 'Action', 'Adventure', 'Science Fiction', 'Thriller', 'Adventure', 'Science Fiction', 'Thriller', 'Action', 'Adventure', 'Science Fiction', 'Fantasy', 'Action', 'Crime', 'Thriller', 'Western', 'Drama', 'Adventure', 'Thriller', 'Science Fiction', 'Action', 'Thriller', 'Adventure', 'Drama', 'Adventure', 'Science Fiction', 'Family', 'Animation', 'Adventure', 'Comedy', 'Comedy', 'Animation', 'Family', 'Action', 'Adventure', 'Crime', 'Science Fiction', 'Fantasy', 'Action', 'Adventure', 'Drama', 'Science Fiction', 'Action', 'Comedy', 'Science Fiction', 'Action', 'Adventure', 'Science Fiction', 'Crime', 'Drama', 'Mystery', 'Western', 'Crime', 'Action', 'Thriller', 'Science Fiction', 'Action', 'Adventure', 'Romance', 'Fantasy', 'Family', 'Drama', 'War', 'Adventure', 'Science Fiction', 'Action', 'Family', 'Sci

In [24]:
all_unique_genres.sort()
all_unique_genres_dict =  {}
genre_df = pd.DataFrame( { "ID" : range(1, len(all_unique_genres) + 1),
                              "Name" : all_unique_genres} )

all_unique_genres_dict = dict(zip(genre_df['Name'], genre_df['ID']))
print(all_unique_genres_dict)
print(genre_df.head())
print(genre_df.tail())

{'Action': 1, 'Adventure': 2, 'Animation': 3, 'Comedy': 4, 'Crime': 5, 'Documentary': 6, 'Drama': 7, 'Family': 8, 'Fantasy': 9, 'Foreign': 10, 'History': 11, 'Horror': 12, 'Music': 13, 'Mystery': 14, 'N/A': 15, 'Romance': 16, 'Science Fiction': 17, 'TV Movie': 18, 'Thriller': 19, 'War': 20, 'Western': 21}
   ID       Name
0   1     Action
1   2  Adventure
2   3  Animation
3   4     Comedy
4   5      Crime
    ID             Name
16  17  Science Fiction
17  18         TV Movie
18  19         Thriller
19  20              War
20  21          Western


In [25]:
movie_genre_df = pd.DataFrame(columns=["movie_id", "genre_id"])
# movie_director_df.head()

for index , row in movies_df.iterrows():
  movie_id = row['id']
  genres = row['genres']
  # print(movie_id, directors)
  name = clean_encoded_name(genres)
  all_name_in_row = [name.strip() for name in name.split(",")]
  # print(all_name_in_row)
  for names in all_name_in_row:
    # Create a new row as a DataFrame
    # print(movie_id, names, all_unique_directors_dict[names])
    new_row = pd.DataFrame({'movie_id':movie_id , 'genre_id': [all_unique_genres_dict[names]]})
    movie_genre_df = pd.concat([movie_genre_df, new_row], ignore_index=True)
    # print(movie_director_df.head())
    # movie_director_df = movie_director_df.append({'movie_id': movie_id, 'director_id': all_unique_directors_dict[names]}, ignore_index=True)

print(movie_genre_df.shape)
movie_genre_df.head(15)




(26983, 2)


movie_id genre_id
0    135397        1
1    135397        2
2    135397       17
3    135397       19
4     76341        1
5     76341        2
6     76341       17
7     76341       19
8    262500        2
9    262500       17
10   262500       19
11   140607        1
12   140607        2
13   140607       17
14   140607        9

In [26]:
prod_comp_lst = movies_df['production_companies'].tolist()
print(len(prod_comp_lst))

10866


In [27]:
special_chars = []
all_prod_comps = []
for named in prod_comp_lst:
  flag = 0
  # name = named
  name = clean_encoded_name(named)
  all_names = [name.strip() for name in name.split(",")]
  for i in range(len(name)):
    val = ord(name[i])
    if (val >= 65 and val <= 90) or (val >= 97 and val <= 122) or name[i] in [" ", ",", "."]:
      continue
    else:
      flag = 1
      if i + 1 < len(name) :
        new_val = ord(name[i+1])
        new_str = ""
        if not ( (new_val >= 65 and new_val <= 90) or (new_val >= 97 and new_val <= 122) or name[i+1] in [" ", ",", "."] ):
          new_str = name[i] + name[i+1]
          special_chars.append(new_str)
        else:
          special_chars.append(name[i])
      else:
        special_chars.append(name[i])
      # break
  if flag == 1:
    pass
    # print(name)
  all_prod_comps.extend(all_names)

new_spec_chars = list(set(special_chars))
print(len(special_chars), special_chars)
print(len(new_spec_chars), new_spec_chars)
print(len(all_prod_comps), all_prod_comps)

all_unique_prod_comps = list(set(all_prod_comps))
print(len(all_unique_prod_comps), all_unique_prod_comps)

  # if "," in name:
  #   names = name.split(',')
  # else:
  #   names = [name]
  # Ã¡ Ã\ Ã¨ Ã³ Ã© Ã¶ Ã¥

6240 ['24', '4', '(', ')', '4', '6', '+', 'é+', '+', '11', '13', '3', '-', '/', '-', '-', '(', ')', '20', '00', '00', '0', '24', '4', '-', '7', '36', '60', '0', '-', '/', '20', '00', '00', '0', '/', '4', '9', '20', '00', '00', '0', '3', 'é', 'é', 'é', '(', ')', '&', '-', '-', '-', '(', ')', '-', '(', ')', '(', ')', '-', '(', ')', '20', '00', '00', '0', '-', '-', '(', ')', '-', '40', '0', '5', '/', '20', '00', '00', '0', '(', ')', '(', ')', '-', '/', "'", '-', '!', '(', ')', '4', '-', '-', '(', ')', '(', ')', 'é', 'ó', 'đ', '(', ')', '1', '+', 'í', '(', ')', '-', '-', '(', ')', '(', ')', 'ó', '19', '98', '84', '4', "'", '(', ')', 'Ā', '(', ')', '24', '4', 'é', '4', '24', '4', '-', '4', '(', ')', '/', '24', '4', '(', ')', '34', '43', '3', '/', 'é', '(', ')', '-', '2', '-', '-', '(', ')', 'Ą', 'Ė', '!', 'ó', '26', '60', '0', '/', '7', '-', '4', "'", '36', '60', '0', '(', ')', '/', '-', '3', '40', '0', '&', '&', '10', '08', '8', '-', '/', '/', '&', '3', '2', '/', '33', '3', '14', '44', '40

In [28]:
all_unique_prod_comps.sort()
all_unique_prod_comps_dict =  {}
prod_comp_df = pd.DataFrame( { "ID" : range(1, len(all_unique_prod_comps) + 1),
                              "Name" : all_unique_prod_comps} )

all_unique_prod_comps_dict = dict(zip(prod_comp_df['Name'], prod_comp_df['ID']))
print(all_unique_prod_comps_dict)
print(prod_comp_df.head())
print(prod_comp_df.tail(10))

{'': 1, '"DIA" Productions GmbH & Co. KG': 2, '# Lexyn Productions': 3, '10 West Studios': 4, '100 Feet Productions': 5, '1019 Entertainment': 6, '108 Media': 7, '10th Hole Productions': 8, '11:11 Mediaworks': 9, '12 Gauge Productions': 10, '120dB Films': 11, '13 Ghosts Productions Canada Inc.': 12, '1492 Pictures': 13, '1600 Limited Partnership': 14, '1812 Productions': 15, '1818': 16, '1821 Pictures': 17, '185 Trax': 18, '1976 Productions': 19, '1984 Private Defense Contractors': 20, '1992 Number Four Limited Partnership': 21, '2 Bridges Productions': 22, '2 Entertain': 23, '2 Entertain Video': 24, '2 Loop Films': 25, '2 Player Productions': 26, '2 Wolves Films': 27, '2.4.7. Films': 28, '2003 Productions': 29, '20ten Media': 30, '20th Century Fox': 31, '20th Century Fox Film Corporation': 32, '20th Century Fox Home Entertainment': 33, '20th Century Fox Russia': 34, '20th Century Fox Television': 35, '20th Century Pictures': 36, '21 Laps Entertainment': 37, '21st Century Film Corporat

In [29]:
movie_prod_comps_df = pd.DataFrame(columns=["movie_id", "prod_comp_id"])

for index , row in movies_df.iterrows():
  movie_id = row['id']
  prod_comps = row['production_companies']
  name = clean_encoded_name(prod_comps)
  all_name_in_row = [name.strip() for name in name.split(",")]
  for names in all_name_in_row:
    new_row = pd.DataFrame({'movie_id':movie_id , 'prod_comp_id': [all_unique_prod_comps_dict[names]]})
    movie_prod_comps_df = pd.concat([movie_prod_comps_df, new_row], ignore_index=True)
print(movie_prod_comps_df.shape)
movie_prod_comps_df.head(15)




(24376, 2)


movie_id prod_comp_id
0    135397         7387
1    135397          351
2    135397         4005
3    135397         2794
4    135397         1925
5     76341         7489
6     76341         3786
7    262500         6707
8    262500         4375
9    262500         5812
10   262500         4888
11   140607         4196
12   140607         7250
13   140607          717
14   168259         7381

In [30]:
keyword_lst = movies_df['keywords'].tolist()
print(len(keyword_lst))

10866


In [31]:
special_chars = []
all_keywords = []
for named in keyword_lst:
  flag = 0
  # name = named
  name = clean_encoded_name(named)
  all_names = [name.strip() for name in name.split(",")]
  for i in range(len(name)):
    val = ord(name[i])
    if (val >= 65 and val <= 90) or (val >= 97 and val <= 122) or name[i] in [" ", ",", "."]:
      continue
    else:
      flag = 1
      if i + 1 < len(name) :
        new_val = ord(name[i+1])
        new_str = ""
        if not ( (new_val >= 65 and new_val <= 90) or (new_val >= 97 and new_val <= 122) or name[i+1] in [" ", ",", "."] ):
          new_str = name[i] + name[i+1]
          special_chars.append(new_str)
        else:
          special_chars.append(name[i])
      else:
        special_chars.append(name[i])
      # break
  if flag == 1:
    pass
    # print(name)
  all_keywords.extend(all_names)

new_spec_chars = list(set(special_chars))
print(len(special_chars), special_chars)
print(len(new_spec_chars), new_spec_chars)
print(len(all_keywords), all_keywords)

all_unique_keywords = list(set(all_keywords))
print(len(all_unique_keywords), all_unique_keywords)

  # if "," in name:
  #   names = name.split(',')
  # else:
  #   names = [name]
  # Ã¡ Ã\ Ã¨ Ã³ Ã© Ã¶ Ã¥

2807 ['-', '3', '-', '3', '3', '3', '3', '-', '3', '-', '3', '17', '7', "'", '-', '3', '19', '97', '70', '0', '66', '6', '-', '-', '-', '/', '-', "'", "'", "'", '/', '19', '97', '70', '0', '/', '/', '/', '/', '/', "'", '/', '/', '-', '/', '/', '/', '-', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', "'", '/', '19', '97', '70', '0', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '51', '1', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/', '/', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '-', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '/', '-', '/', '/', '/

In [32]:
all_unique_keywords.sort()
all_unique_keywords_dict =  {}
keyword_df = pd.DataFrame( { "ID" : range(1, len(all_unique_keywords) + 1),
                              "Name" : all_unique_keywords} )

all_unique_keywords_dict = dict(zip(keyword_df['Name'], keyword_df['ID']))
print(all_unique_keywords_dict)
print(keyword_df.head())
print(keyword_df.tail(10))

{'12th century': 1, '15th century': 2, '16th century': 3, '17th century': 4, '18th century': 5, '1910s': 6, '1920s': 7, '1930s': 8, '1960s': 9, '1970s': 10, '1980s': 11, '1990s': 12, '19th century': 13, '217095': 14, '3d': 15, '3d animation': 16, 'N/A': 17, 'aaron swartz': 18, 'abduction': 19, 'absent  mother': 20, 'abuse': 21, 'accepting death': 22, 'accident': 23, 'accidental crime': 24, 'accidental love': 25, 'action': 26, 'activist': 27, 'actor': 28, 'actress': 29, 'addict': 30, 'addicted': 31, 'addiction': 32, 'admiral': 33, 'admiration': 34, 'admissions': 35, 'adolescence': 36, 'adolescent boy': 37, 'adolf hitler': 38, 'adopted': 39, 'adoption': 40, 'adoptive father': 41, 'adoptive mother': 42, 'adult': 43, 'adult animation': 44, 'adult as a child': 45, 'adultery': 46, 'advancement': 47, 'adventure': 48, 'adventurer': 49, 'adversary': 50, 'advertising executive': 51, 'advertising expert': 52, 'advice': 53, 'advocacy': 54, 'aerial shot': 55, 'aerobics': 56, 'affair': 57, 'affectio

In [33]:
movie_keyword_df = pd.DataFrame(columns=["movie_id", "keyword_id"])

for index , row in movies_df.iterrows():
  movie_id = row['id']
  keywords = row['keywords']
  name = clean_encoded_name(keywords)
  all_name_in_row = [name.strip() for name in name.split(",")]
  for names in all_name_in_row:
    new_row = pd.DataFrame({'movie_id':movie_id , 'keyword_id': [all_unique_keywords_dict[names]]})
    movie_keyword_df = pd.concat([movie_keyword_df, new_row], ignore_index=True)

print(movie_keyword_df.shape)
movie_keyword_df.head(15)

(38944, 2)


movie_id keyword_id
0    135397       4554
1    135397       1999
2    135397       7369
3    135397       7490
4    135397       3653
5     76341       2823
6     76341       1210
7     76341       5424
8     76341       2162
9     76341        398
10   262500        543
11   262500       5883
12   262500       2162
13   262500       6246
14   262500       2163

#### Preparing data for database and inserting

In [34]:
movies_df.columns

Index(['id', 'imdb_id', 'popularity', 'budget', 'revenue', 'original_title',
       'cast', 'homepage', 'director', 'tagline', 'keywords', 'overview',
       'runtime', 'genres', 'production_companies', 'release_date',
       'vote_count', 'vote_average', 'release_year', 'budget_adj',
       'revenue_adj'],
      dtype='object')

In [35]:
final_movies_df = movies_df[['id','imdb_id','popularity', 'budget', 'revenue', 'original_title', 'homepage',
                            'tagline', 'overview', 'runtime', 'release_date', 'vote_count', 'vote_average',
                            'release_year', 'budget_adj', 'revenue_adj']]

In [36]:
access_dict = {"Admin":1, "User":2}

access_df = pd.DataFrame({"ID":access_dict.values(), "Name":access_dict.keys()})
print(access_df)

   ID   Name
0   1  Admin
1   2   User


In [37]:
!pip install cryptography

In [38]:
from cryptography.fernet import Fernet

key = Fernet.generate_key()
cipher_suite = Fernet(key)

user_account_name = ["sss@de.com", "guest@de.com"]
user_password_hash = ["abcdef", "guest"]
access_id = [1, 2]
date_of_birth = ["", ""]

encrypted_passwords = [cipher_suite.encrypt(password.encode()).decode() for password in user_password_hash]

user_account_df = pd.DataFrame({
    "ID": [1, 2],
    "username": user_account_name,
    "password": encrypted_passwords,
    "access_id": access_id,
    "DOB": date_of_birth
})

print("DataFrame with Encrypted Passwords:")
print(user_account_df)


DataFrame with Encrypted Passwords:
   ID      username                                           password  \
0   1    sss@de.com  gAAAAABnN0Uw-sRkPAH2rXFOuQGh-JZ7FHxzci271Oz7oI...   
1   2  guest@de.com  gAAAAABnN0UwxuLwYcWnq0h8g47DpiStocgWOnw7lC037h...   

   access_id DOB  
0          1      
1          2      


In [1]:
!pip install SQLAlchemy
!pip install psycopg2

In [39]:
import pandas as pd
from sqlalchemy import create_engine
import psycopg2

In [40]:
# Define PostgreSQL connection details
db_name = 'movies_de_database'
db_user = 'postgres'
db_password = 'qwertyuiop'
db_host = 'localhost'  # or your DB server IP
db_port = '5432'  # default PostgreSQL port

# Create a new PostgreSQL database connection
conn = psycopg2.connect(dbname='postgres', user=db_user, password=db_password, host=db_host, port=db_port)
conn.autocommit = True
cursor = conn.cursor()





In [41]:
# Print the current database name

# Execute a query to list all tables in the current database
cursor.execute("SELECT table_name FROM information_schema.tables WHERE table_schema='public';")
tables = cursor.fetchall()

print("Tables present in the database:")
for table in tables:
    print(table[0])

Tables present in the database:


In [ ]:
cursor.execute("SELECT 1 FROM pg_database WHERE LOWER(datname) = LOWER(%s);", (db_name,))
exists = cursor.fetchone()

if not exists:
    cursor.execute(f"CREATE DATABASE {db_name}")
    print(f"Database '{db_name}' created successfully!")
else:
    print(f"Database '{db_name}' already exists.")

Database 'movies_de_database' already exists.


In [44]:
# Connect to the newly created database
engine = create_engine(f'postgresql+psycopg2://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}')


# Connect to the newly created or existing database
conn = psycopg2.connect(dbname=db_name, user=db_user, password=db_password, host=db_host, port=db_port)
cursor = conn.cursor()

# Execute a query to get the list of databases
cursor.execute("SELECT datname FROM pg_database;")
databases = cursor.fetchall()

print("Databases present:")
for database in databases:
    print(database[0])

Databases present:
postgres
template1
template0
iit_palakkad
movies_de_database


In [ ]:

table_name = 'movies'  # choose a table name
final_movies_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

In [86]:
# Print the current database name
print("Connected to database:", conn.get_dsn_parameters()['dbname'])

# Execute a query to list all tables in the current database
cursor.execute("SELECT table_name FROM information_schema.tables WHERE table_schema='public';")
tables = cursor.fetchall()

print("Tables present in the database:")
for table in tables:
    print(table[0])

Connected to database: movies_de_database
Tables present in the database:
movies
keywords
movie_keywords
actors
movie_actors
genres
movie_genres
directors
movie_directors
prod_companies
movie_prod_companies
access_detail
user_account


In [138]:

# Create a table and insert data into the new database
table_name = 'keywords'  # choose a table name
keyword_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'keywords' table in the 'movies_de_database' database!


In [139]:

# Create a table and insert data into the new database
table_name = 'movie_keywords'  # choose a table name
movie_keyword_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'movie_keywords' table in the 'movies_de_database' database!


In [140]:

# Create a table and insert data into the new database
table_name = 'actors'  # choose a table name
actor_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'actors' table in the 'movies_de_database' database!


In [141]:

# Create a table and insert data into the new database
table_name = 'movie_actors'  # choose a table name
movie_actor_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'movie_actors' table in the 'movies_de_database' database!


In [142]:

# Create a table and insert data into the new database
table_name = 'genres'  # choose a table name
genre_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'genres' table in the 'movies_de_database' database!


In [143]:

# Create a table and insert data into the new database
table_name = 'movie_genres'  # choose a table name
movie_genre_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'movie_genres' table in the 'movies_de_database' database!


In [146]:

# Create a table and insert data into the new database
table_name = 'directors'  # choose a table name
director_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'directors' table in the 'movies_de_database' database!


In [147]:

# Create a table and insert data into the new database
table_name = 'movie_directors'  # choose a table name
movie_director_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'movie_directors' table in the 'movies_de_database' database!


In [148]:

# Create a table and insert data into the new database
table_name = 'prod_companies'  # choose a table name
prod_comp_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'prod_companies' table in the 'movies_de_database' database!


In [ ]:

# Create a table and insert data into the new database
table_name = 'movie_prod_companies'  # choose a table name
movie_prod_comps_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'movie_prod_companies' table in the 'movies_de_database' database!


In [154]:

# Create a table and insert data into the new database
table_name = 'access_detail'  # choose a table name
access_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'access_detail' table in the 'movies_de_database' database!


In [155]:

# Create a table and insert data into the new database
table_name = 'user_account'  # choose a table name
user_account_df.to_sql(table_name, engine, if_exists='replace', index=False)

print(f"Data successfully inserted into the '{table_name}' table in the '{db_name}' database!")

Data successfully inserted into the 'user_account' table in the 'movies_de_database' database!


1. Who are the top 5 directors by the number of movies they have directed?

In [68]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT d."Name", COUNT(md.movie_id) AS movie_count
FROM directors AS d , movie_directors AS md
WHERE d."ID" = md.director_id
GROUP BY d."Name"
ORDER BY movie_count DESC
LIMIT 5;
"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Woody Allen', 46)
('N/A', 44)
('Clint Eastwood', 34)
('Martin Scorsese', 31)
('Steven Spielberg', 30)


2. Which are the top 5 movies with the highest profit margin (revenue-to-budget ratio)?

In [70]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT original_title, (revenue / budget) AS profit_margin
FROM movies
WHERE budget > 0  -- To avoid division by zero
ORDER BY profit_margin DESC
LIMIT 5;
"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('The Karate Kid, Part II', 1018619)
('Into the Night', 58771)
('From Prada to Nada', 26881)
('Paranormal Activity', 12890)
('The Blair Witch Project', 9920)


3. Which directors have the most movies in the top 100 grossing films?

In [72]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT d."Name" AS director_name, COUNT(m.id) AS movie_count
FROM directors AS d , movie_directors AS md , movies AS m
WHERE d."ID" = md.director_id AND md.movie_id = m.id
AND m.id IN (
    SELECT id
    FROM movies
    WHERE revenue IS NOT NULL
    ORDER BY revenue DESC
    LIMIT 100
)
GROUP BY d."Name"
ORDER BY movie_count DESC
LIMIT 5;
"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Peter Jackson', 6)
('George Lucas', 4)
('David Yates', 4)
('Christopher Nolan', 4)
('Francis Lawrence', 3)


4. Which actors have the highest average vote in Sci-Fi movies?


In [73]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT a."Name" AS actor_name, AVG(m.vote_average) AS average_vote
FROM actors AS a , movie_actors AS ma , movies AS m , movie_genres AS mg , genres AS g
WHERE a."ID" = ma.actor_id AND ma.movie_id = m.id AND m.id = mg.movie_id 
AND mg.genre_id = g."ID"  -- Ensure correct case for genre ID
AND g."Name" = 'Science Fiction' -- Filter for Sci-Fi genre
GROUP BY a."Name"
ORDER BY average_vote DESC
LIMIT 5;
"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Oona Chaplin', 8.8)
('Janet Montgomery', 8.8)
('Jon Hamm', 8.8)
('Rafe Spall', 8.8)
('Winona Mae', 8.2)


5. For each director, which actor have they collaborated with the most, and what is the
highest-grossing movie from their collaboration?

In [87]:
# Query to select the first 5 rows from the "Movies" table
query = """
WITH highest_grossing_movies AS (
    SELECT id AS movie_id, original_title, revenue
    FROM movies
    WHERE revenue IS NOT NULL
    ORDER BY revenue DESC
    -- LIMIT 100  -- You can adjust the number of movies you want to consider
)

SELECT d."Name" AS director_name,
       a."Name" AS actor_name,
       COUNT(*) AS total_collaborations,
       hgm.original_title,
       hgm.revenue
FROM highest_grossing_movies AS hgm, movie_directors AS md ,
 directors AS d , movie_actors AS ma, actors AS a
WHERE hgm.movie_id = md.movie_id AND md.director_id = d."ID"
AND hgm.movie_id = ma.movie_id AND ma.actor_id = a."ID"
GROUP BY d."Name", a."Name", hgm.original_title, hgm.revenue
ORDER BY revenue Desc, director_name, actor_name
LIMIT 5;

"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('James Cameron', 'Michelle Rodriguez', 1, 'Avatar', 2781505847)
('James Cameron', 'Sam Worthington', 1, 'Avatar', 2781505847)
('James Cameron', 'Sigourney Weaver', 1, 'Avatar', 2781505847)
('James Cameron', 'Stephen Lang', 1, 'Avatar', 2781505847)
('James Cameron', 'Zoe Saldana', 1, 'Avatar', 2781505847)


6. Is there a correlation between higher popularity scores and higher box office revenue
across different genres?

In [ ]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT g."Name" AS genre_name,
       AVG(m.popularity) AS average_popularity,
       AVG(m.revenue) AS average_revenue
FROM movies AS m, movie_genres AS mg , genres AS g 
WHERE m.id = mg.movie_id AND mg.genre_id = g."ID"
AND m.revenue IS NOT NULL AND m.popularity IS NOT NULL
GROUP BY g."Name"
ORDER BY g."Name";


"""

sql_df = pd.read_sql(query, engine)

# Debugging: Check the DataFrame columns
print("Columns in DataFrame:", sql_df.columns)

# Calculate correlation between average popularity and average revenue
correlation = sql_df['average_popularity'].corr(sql_df['average_revenue'])

# Print the results
print("Average Popularity and Revenue per Genre:")
print(sql_df)
print("\nCorrelation between average popularity and average revenue:", correlation)



Columns in DataFrame: Index(['genre_name', 'average_popularity', 'average_revenue'], dtype='object')
Average Popularity and Revenue per Genre:
         genre_name  average_popularity  average_revenue
0            Action            1.252599     7.270446e+07
1         Adventure            1.314917     1.131379e+08
2         Animation            1.232496     7.525606e+07
3            Comedy            1.161673     3.752624e+07
4             Crime            1.203144     4.227713e+07
5       Documentary            1.049485     2.041107e+06
6             Drama            1.161370     2.921445e+07
7            Family            1.214621     7.243318e+07
8           Fantasy            1.270874     9.631366e+07
9           Foreign            1.052231     1.520460e+06
10          History            1.157124     3.201179e+07
11           Horror            1.126953     1.682281e+07
12            Music            1.132946     2.857177e+07
13          Mystery            1.188249     4.021757e+07
14

7. Which actors have the highest difference between their average ratings in Drama vs.
Comedy movies?

In [91]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT a."Name" AS actor_name,
       COALESCE(AVG(CASE WHEN g."Name" = 'Drama' THEN m.vote_average END), 0) AS average_drama_rating,
       COALESCE(AVG(CASE WHEN g."Name" = 'Comedy' THEN m.vote_average END), 0) AS average_comedy_rating,
       ABS(COALESCE(AVG(CASE WHEN g."Name" = 'Drama' THEN m.vote_average END), 0) -
                COALESCE(AVG(CASE WHEN g."Name" = 'Comedy' THEN m.vote_average END), 0)) AS rating_difference
FROM actors AS a , movie_actors AS ma , movies AS m , genres AS g ,movie_genres AS mg
WHERE a."ID" = ma.actor_id AND ma.movie_id = m.id AND m.id = mg.movie_id
AND  mg.genre_id = g."ID"
GROUP BY a."Name"
ORDER BY rating_difference DESC
LIMIT 5;

"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Janet Montgomery', 8.8, 0.0, 8.8)
('Oona Chaplin', 8.8, 0.0, 8.8)
('Franziska Kruse', 8.4, 0.0, 8.4)
('Shaun Ross', 8.4, 0.0, 8.4)
('Rüdiger Evers', 8.4, 0.0, 8.4)


8. Which are the top 5 production companies by total revenue across different genres?


In [92]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT pc."Name" AS production_company_name,
       SUM(m.revenue) AS total_revenue
FROM prod_companies AS pc , movie_prod_companies AS mpc , movies AS m
WHERE pc."ID" = mpc.prod_comp_id AND  mpc.movie_id = m.id
AND m.revenue IS NOT NULL
GROUP BY pc."Name"
ORDER BY total_revenue DESC
LIMIT 5;

"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Warner Bros.', Decimal('54688433698'))
('Universal Pictures', Decimal('48134982923'))
('Paramount Pictures', Decimal('41348789455'))
('Twentieth Century Fox Film Corporation', Decimal('37828180788'))
('Walt Disney Pictures', Decimal('32611388637'))


9. Which actors have the most appearances in high-rated movies across different genres?

In [93]:
# Query to select the first 5 rows from the "Movies" table
query = """
SELECT a."Name" AS actor_name,
       g."Name" AS genre_name,
	   COUNT(CASE WHEN m.vote_average > 9 THEN ma.movie_id END) AS above_9_count,
       COUNT(CASE WHEN m.vote_average > 8 THEN ma.movie_id END) AS above_8_count,
       COUNT(CASE WHEN m.vote_average > 7 THEN ma.movie_id END) AS above_7_count,
       COUNT(CASE WHEN m.vote_average > 6 THEN ma.movie_id END) AS above_6_count,
       COUNT(CASE WHEN m.vote_average > 5 THEN ma.movie_id END) AS above_5_count,
       COUNT(CASE WHEN m.vote_average < 5 THEN ma.movie_id END) AS below_5_count
FROM actors AS a, movie_actors AS ma, movies AS m, movie_genres AS mg ,genres AS g
WHERE a."ID" = ma.actor_id AND ma.movie_id = m.id AND m.id = mg.movie_id
AND mg.genre_id = g."ID"
GROUP BY a."Name", g."Name"
ORDER BY above_9_count DEsc, above_8_count DEsc, above_7_count DEsc , 
above_6_count DEsc, above_5_count DEsc,below_5_count DEsc
LIMIT 5;

"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Cari Beauchamp', 'Documentary', 1, 1, 1, 1, 1, 0)
('Jean-Michel Frodon', 'Documentary', 1, 1, 1, 1, 1, 0)
('Mark Cousins', 'Documentary', 1, 1, 1, 1, 1, 0)
('Agnes de Mille', 'Documentary', 1, 1, 1, 1, 1, 0)
('N/A', 'Documentary', 0, 4, 21, 34, 41, 1)


10. Which genres have the most profitable sequels and prequels?

In [94]:
# Query to select the first 5 rows from the "Movies" table
query = """
WITH sequel_prequel_profits AS (
    SELECT g."Name" AS genre_name,
           m.original_title AS movie_name,
           (m.revenue - m.budget) AS profit
    FROM movies AS m
    JOIN movie_genres AS mg ON m.id = mg.movie_id
    JOIN genres AS g ON mg.genre_id = g."ID"
    WHERE m.original_title ~ '.*[1-9]$' -- Matches movie names ending with any integer from 1 to 9
    OR m.original_title LIKE '%10' -- Specifically check for '10'
    AND m.revenue IS NOT NULL AND m.budget IS NOT NULL
)
SELECT genre_name,
       SUM(profit) AS total_profit,
       STRING_AGG(movie_name, ', ') AS movie_names
FROM sequel_prequel_profits
GROUP BY genre_name
ORDER BY total_profit DESC;


"""
cursor.execute(query)

# Fetch all results
rows = cursor.fetchall()

# Print each row
for row in rows:
    print(row)

('Adventure', Decimal('12142713131'), "The Hunger Games: Mockingjay - Part 2, Paul Blart: Mall Cop 2, The Hunger Games: Mockingjay - Part 1, Big Hero 6, The Amazing Spider-Man 2, How to Train Your Dragon 2, The Expendables 3, Rio 2, Airport '77, 2012, 9, Planet 51, The Descent: Part 2, The Marine 2, Iron Man 2, Harry Potter and the Deathly Hallows: Part 1, Flicka 2, K-911, Transporter 3, Ong Bak 2, Open Season 2, The Sisterhood of the Traveling Pants 2, Harry Potter and the Deathly Hallows: Part 2, Cars 2, The Twilight Saga: Breaking Dawn - Part 1, Scrat's Continental Crack-Up: Part 2, Stuart Little 2, The Expendables 2, The Twilight Saga: Breaking Dawn - Part 2, The Jungle Book 2, George of the Jungle 2, Inspector Gadget 2, X2, Iron Man 3, Kick-Ass 2, Death Wish 3, Cheaper by the Dozen 2, Brother Bear 2, The Fox and the Hound 2, Shrek 2, Spider-Man 2, Zenon: Z3, Spider-Man 3, Lethal Weapon 3, Passenger 57, Mad Max 2, All Dogs Go to Heaven 2, Daai laap mat taam 008, Lethal Weapon 4, Le

#### Triggers used

In [ ]:
query = """CREATE OR REPLACE FUNCTION update_movie_similarity()
RETURNS TRIGGER AS $$
BEGIN
    INSERT INTO movie_similarity (movie_id_1, movie_id_2, similarity_score)
    SELECT 
        LEAST(NEW.id, m.id) AS movie_id_1,
        GREATEST(NEW.id, m.id) AS movie_id_2,
        similarity(NEW.original_title, m.original_title) AS similarity_score
    FROM movies m
    WHERE NEW.id != m.id
      AND similarity(NEW.original_title, m.original_title) > 0.5
      AND similarity(NEW.original_title, m.original_title) < 1;

    RETURN NEW;
END;
$$ LANGUAGE plpgsql;

CREATE OR REPLACE TRIGGER after_movie_insert
AFTER INSERT ON movies
FOR EACH ROW
EXECUTE FUNCTION update_movie_similarity();
"""

cursor.execute(query)

In [ ]:
query = """CREATE OR REPLACE FUNCTION delete_movie_from_similarity()
RETURNS TRIGGER AS $$
BEGIN
    DELETE FROM movie_similarity
    WHERE movie_id_1 = OLD.id OR movie_id_2 = OLD.id;

    RETURN OLD;
END;
$$ LANGUAGE plpgsql;


CREATE OR REPLACE TRIGGER after_movie_delete
AFTER DELETE ON movies
FOR EACH ROW
EXECUTE FUNCTION delete_movie_from_similarity();

"""

cursor.execute(query)

In [22]:
cursor.close()
conn.close()